In [11]:
import json
import os
import requests
import numpy as np

import geopandas as gpd
import folium
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd

In [12]:
import requests
# regions = requests.get('https://maps.amsterdam.nl/open_geodata/geojson_lnglat.php?KAARTLAAG=INDELING_GEBIED&THEMA=gebiedsindeling').json()
regions = requests.get('https://maps.amsterdam.nl/open_geodata/geojson_lnglat.php?KAARTLAAG=INDELING_STADSDEEL&THEMA=gebiedsindeling').json()

In [13]:
base_url = "https://sidewalk-amsterdam.cs.washington.edu/v2/access/attributesWithLabels?lat1={}&lng1={}&lat2={}&lng2={}" 
whole = (52.303, 4.8, 52.425, 5.05)
centrum_west = (52.364925, 4.87444, 52.388692, 4.90641)

coords = centrum_west

url = base_url.format(*coords)

local_dump = url.replace('/', '|')

try:
    project_sidewalk_labels = json.load(open(local_dump, 'r'))
except Exception as e:
    print("Couldn't load local dump")
    project_sidewalk_labels = requests.get(url.format(*coords)).json()
    json.dump(project_sidewalk_labels, open(local_dump, 'w'))

In [14]:
# Open https://maps.amsterdam.nl/open_geodata/geojson_lnglat.php?KAARTLAAG=INDELING_WIJK&THEMA=gebiedsindeling and make a
# geopandas dataframe from it
data = requests.get('https://maps.amsterdam.nl/open_geodata/geojson_lnglat.php?KAARTLAAG=INDELING_WIJK&THEMA=gebiedsindeling').json()
gdf = gpd.GeoDataFrame.from_features(data['features'])
Gebiedsindeling = gdf['Gebied'].unique()
Gebiedsindeling

# Select the Gebied "Centrum-West" rows
gdf_centrum_west = gdf[gdf['Gebied'] == 'Centrum-West']
gdf_centrum_west

geometry CBS_Wijkcode Wijkcode  \
21  POLYGON ((4.88167 52.38418, 4.88254 52.38392, ...     BU0363AA       AA   
23  POLYGON ((4.87549 52.37341, 4.87543 52.37324, ...     BU0363AB       AB   
24  POLYGON ((4.88621 52.37809, 4.88316 52.37475, ...     BU0363AC       AC   
41  POLYGON ((4.89131 52.37632, 4.89118 52.37619, ...     BU0363AD       AD   
42  POLYGON ((4.89969 52.37730, 4.89914 52.37697, ...     BU0363AE       AE   

                       Wijk Gebiedcode        Gebied Stadsdeelcode Stadsdeel  \
21          Haarlemmerbuurt       GA01  Centrum-West             A   Centrum   
23                  Jordaan       GA01  Centrum-West             A   Centrum   
24      Grachtengordel-West       GA01  Centrum-West             A   Centrum   
41  Burgwallen-Nieuwe Zijde       GA01  Centrum-West             A   Centrum   
42    Burgwallen-Oude Zijde       GA01  Centrum-West             A   Centrum   

    Oppervlakte_m2  
21          811434  
23          942953  
24          566891  
41          725676  
42          403162

In [15]:
# Join the polygons of Gebied "Centrum-West" to a unique polygon
gdf_centrum_west = gdf_centrum_west.dissolve(by='Gebied')
gdf_centrum_west

# Find the bounds of the polygon
gdf_centrum_west.bounds

minx       miny     maxx       maxy
Gebied                                              
Centrum-West  4.87444  52.364925  4.90641  52.388692

In [16]:
# Define the lat/lon coordinates of the region
coords = [[4.87444 , 52.364925],  [4.90641, 52.388692]]
# Reverse the x and y
coords = [[c[1], c[0]] for c in coords]
print(coords)
#coords = [[52.378766, 4.881667], [52.388692, 4.898773]]

# Create a map centered on the mean of the coordinates
center = [sum([c[0] for c in coords])/2, sum([c[1] for c in coords])/2]
m = folium.Map(location=center, zoom_start=15)

# Add a rectangle to the map representing the region
folium.Rectangle(bounds=coords, color='red', fill=True, fill_opacity=0.2).add_to(m)

# Show the map
m

[[52.364925, 4.87444], [52.388692, 4.90641]]


In [17]:
# Only keep labels from "Centrum-West" neighbourhood, and print length before and after
ps_labels_df = gpd.GeoDataFrame.from_features(project_sidewalk_labels['features'])
# Print length before filtering
print('Length before filtering:', len(ps_labels_df))

Length before filtering: 1793


In [18]:
# Script to visualize all the datapoints from both Project Sidewalk labels and the ones we generated from our model

od_labels_path = pd.read_csv('res/dataset/centrum_west_small/backprojected/object_locations.csv')

# Convert od_labels_path to a geopandas dataframe
od_labels_df = gpd.GeoDataFrame(od_labels_path, geometry=gpd.points_from_xy(od_labels_path.lon, od_labels_path.lat))

ps_labels_df = ps_labels_df[ps_labels_df['label_type'] == 'Obstacle']
ps_labels_df = ps_labels_df[ps_labels_df['image_date'] > '2021-01']

ps_labels_df


geometry  attribute_id label_type  street_edge_id  \
3     POINT (4.90542 52.37830)        247961   Obstacle           23691   
4     POINT (4.89085 52.37085)        247096   Obstacle            7382   
5     POINT (4.88440 52.36686)        250177   Obstacle            8154   
8     POINT (4.88440 52.36686)        250177   Obstacle            8154   
9     POINT (4.88425 52.36683)        250176   Obstacle            8154   
...                        ...           ...        ...             ...   
1715  POINT (4.89069 52.37108)        247100   Obstacle            7383   
1720  POINT (4.88687 52.37331)        247439   Obstacle            8001   
1749  POINT (4.88824 52.36904)        253314   Obstacle           28337   
1760  POINT (4.88814 52.36871)        253315   Obstacle           21430   
1773  POINT (4.88328 52.37238)        247487   Obstacle            8094   

      osm_street_id        neighborhood  severity  is_temporary  label_id  \
3         314087588  Stationsplein e.o.       5.0          True       314   
4           7371259      Begijnhofbuurt       2.0         False       446   
5           7372844  Leidsegracht Noord       4.0         False       450   
8           7372844  Leidsegracht Noord       4.0         False       461   
9           7372844  Leidsegracht Noord       3.0         False       464   
...             ...                 ...       ...           ...       ...   
1715        7371261      Begijnhofbuurt       4.0         False       438   
1720        7372583  Felix Meritisbuurt       5.0         False       676   
1749      562720340     Spuistraat Zuid       3.0         False     15530   
1760      164217709     Spuistraat Zuid       3.0         False     13000   
1773        7372703  Felix Meritisbuurt       3.0         False     15078   

             gsv_panorama_id  ...  image_date               label_date  \
3     DrIPNFIUCgde9jC7K8gfpg  ...     2022-01  2022-02-27 14:45:06.007   
4     b47UnNbbYK8LFapUL5yJNQ  ...     2021-03  2022-03-01 17:16:08.373   
5     SeYsQO8U9o5Af3ZJYzgpHQ  ...     2021-03  2022-03-01 17:17:09.528   
8     vkmyQT2j2dEmG8C0VW6FkA  ...     2021-03  2022-03-01 17:18:18.557   
9     7WhU4TGc52yL7fXuzRhUYg  ...     2021-03  2022-03-01 17:18:37.373   
...                      ...  ...         ...                      ...   
1715  CQzIaYhjaTonxJhl0DE6ZA  ...     2021-03  2022-03-01 17:14:46.484   
1720  LHxLaFyA5AOSkOpIoOyKsA  ...     2021-09  2022-03-02 14:20:22.788   
1749  Vx3NN07M8NLu28Kptk3hdg  ...     2021-09  2022-03-31 19:23:41.628   
1760  xbYPv0uztbPU-uBBprjI0A  ...     2021-03  2022-03-30 11:58:37.761   
1773  Nxzh8l7BdQizZ9mlc3odLg  ...     2021-08  2022-03-31 17:01:49.896   

      label_severity  label_is_temporary  agree_count  disagree_count  \
3                5.0                True            4               1   
4                2.0               False            5               0   
5                4.0               False            6               0   
8                4.0               False            5               1   
9                NaN               False            5               0   
...              ...                 ...          ...             ...   
1715             4.0               False            4               1   
1720             5.0               False            5               0   
1749             3.0               False            2               0   
1760             3.0               False            0               0   
1773             3.0               False            2               1   

      notsure_count      label_tags label_description  \
3                 0  [construction]              None   
4                 1          [pole]              None   
5                 0   [parked bike]              None   
8                 0          [pole]              None   
9                 0   [parked bike]              None   
...             ...             ...               ...   
1715              1            

In [19]:
hmap = folium.Map(location=[52.3676, 4.90], zoom_start=12, tiles='stamentoner',)

# Each row of ps_labels_df contains the column "geomtetry", where the coordinates are stored as a POINT(x y). We want
# to extract the x and y coordinates from this column, and add them to the map as a CircleMarker
ps_labels_df.apply(lambda row:folium.CircleMarker(location=[row["geometry"].y, row["geometry"].x], radius=2, color='red').add_to(hmap), axis=1)

# Add od_labels_df to the map
od_labels_df.apply(lambda row:folium.CircleMarker(location=[row["lat"], row["lon"]], radius=2, color='blue').add_to(hmap), axis=1)

hmap

# Save the hmap as a high resolution image
hmap.save('res/dataset/centrum_west_small/heatmap.html')

In [ ]:
# Calculate accuracy, precision and recall considering the labels from Project Sidewalk as ground truth and 
# the labels from our model as predictions

from shapely.geometry import Point

# create a function to add a 5-meter buffer to a Point object
def add_buffer(point):
    return point.buffer(0.000045)

# create a function to add a 1-meter buffer to a Point object
def add_buffer_1m(point):
    return point.buffer(0.000009)

# add a 5-meter buffer to the ground truth points
ps_labels_df['buffered_geometry'] = ps_labels_df.geometry.apply(add_buffer)

# create a function to check if a predicted point (coming from od_labels_df) is inside the buffered ground truth point
def is_inside_buffer(point):
    #print(point)
    for buffer_poly in ps_labels_df.buffered_geometry:
        #print(buffer_poly)
        if point.within(buffer_poly):
            return True
    return False

# add a column to the predicted dataframe to indicate if each prediction is valid
od_labels_df['is_valid'] = od_labels_df.geometry.apply(is_inside_buffer)

# calculate the accuracy, precision, and recall scores
accuracy = np.mean(od_labels_df.is_valid)
precision = np.mean(od_labels_df[od_labels_df.is_valid].index.isin(ps_labels_df.index))
recall = np.mean(ps_labels_df.geometry.apply(lambda x: any(x.within(buffer_poly) for buffer_poly in od_labels_df.buffered_geometry)))


In [ ]:
# Print the accuracy, precision and recall scores
print('Accuracy:', accuracy)
print('Precision:', precision)
print('Recall:', recall)

Accuracy: 1.0
Precision: 1.0
Recall: 0.0016731734523145567


In [46]:
# Visualized the bufferes around the ground truth points (ps_labels_df['buffered_geometry'])
hmap = folium.Map(location=[52.3676, 4.90], zoom_start=12, tiles='stamentoner',)
ps_labels_df.apply(lambda row:folium.CircleMarker(location=[row["geometry"].y, row["geometry"].x], radius=2, color='red').add_to(hmap), axis=1)
ps_labels_df.apply(lambda row:folium.GeoJson(row["buffered_geometry"]).add_to(hmap), axis=1)

# Add the od_labels_df
od_labels_df.apply(lambda row:folium.CircleMarker(location=[row["lat"], row["lon"]], radius=2, color='green').add_to(hmap), axis=1)

hmap